# Earthquake physic and Machine Learning
Group project by Marta Fanti, Giulia Pontesilli, Chiara Tardani

# Abstract

# Functions etc...

Functions needed for plotting data and preparing datasets, imports ...

In [1]:
# getting the data
!git clone https://github.com/martafn04/eqml24.git

Cloning into 'eqml24'...
remote: Enumerating objects: 14, done.
remote: Counting objects: 100% (14/14), done.
remote: Compressing objects: 100% (14/14), done.
remote: Total 14 (delta 2), reused 0 (delta 0), pack-reused 0 (from 0)
Receiving objects: 100% (14/14), 18.59 MiB | 7.74 MiB/s, done.
Resolving deltas: 100% (2/2), done.


In [2]:
# data processing
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler

# graphs
from plotly.subplots import make_subplots
import plotly.express as px
import plotly.graph_objects as go

# models
from keras.layers import BatchNormalization,Flatten,Convolution1D,Activation,Input,Dense,LSTM,Concatenate,Lambda
from keras.callbacks import ModelCheckpoint,EarlyStopping, ReduceLROnPlateau
from keras.saving import load_model, save_model, load_weights, save_weights
from keras import losses, models, optimizers
import tensorflow as tf

# deterministic output
import random as rn
import os
import tensorflow.python.keras.backend as K

In [3]:
def get_AE(exp: int):
  '''
  Loads the acoustic emissions from given experiment
  '''
  path = 'eqml24/'

  if exp == 4581:
    path += 'p4581_3800_to_4100'
  elif exp == 4679:
    path += 'p4679_4340_to_4540'
  elif exp == 5198:
    path += 'p5198_6600_to_6900'
  else:
    raise Exception(f'Experiment p{exp} does not exist.')

  AE = pd.read_csv(f'{path}.csv')
  return AE.drop(columns = 'Unnamed: 0')


def prepare_dataset(data, steps: int, fraction: float, verbose=1):
  '''
  Prepares the training and test dataset from given data
  '''
  train_size = int(data.shape[0] * fraction)
  dataset_train = data[0:train_size]
  train_set = dataset_train.iloc[:, :].values
  dataset_test = data[train_size - steps:len(data)]
  test_set = dataset_test.iloc[:, :].values
  scaler = MinMaxScaler()

  train_scaled = scaler.fit_transform(train_set)
  X_train, y_train = np.zeros((train_size - steps, steps, 2)), np.zeros((train_size - steps))
  for i in range(steps, X_train.shape[0]):
    X_train[i, :, :] = train_scaled[i-steps:i, 4:5] # Var_Ch1 and Var_Ch2
    y_train[i] = train_scaled[i, 2] # ShearStress

  test_scaled = scaler.fit_transform(test_set)
  X_test, y_test = np.zeros((test_set.shape[0] - steps, steps, 2)), np.zeros((test_set.shape[0] - steps))
  for i in range(steps, X_test.shape[0]):
    X_test[i, :, :] = test_scaled[i-steps:i, 4:5]
    y_test[i] = test_scaled[i, 2]

  if verbose == 1:
    print(f'The training set is the {fraction * 100:0.0f}% of the complete dataset (that has shape {AE.shape}).\n\nStarting from a training dataset of shape {dataset_train.shape} we got:\n- X_train with shape {X_train.shape};\n- y_train with shape {y_train.shape}.\n\nOur test dataset was {dataset_test.shape} and we got:\n- X_test that is {X_test.shape};\n- y_test that is {y_test.shape}.')
  return X_train, y_train, X_test, y_test

def error(pred, test):
  '''
  Evaluates the Root Mean Squared Error
  '''
  return np.sqrt(np.mean((pred - test)**2))

# Data
We will be using data from experiments p4581, p4679 and p5198 (that we took from [here](https://elearning.uniroma1.it/mod/folder/view.php?id=678339)).
<br>Here we will be plotting it, and extracting some useful features.

In [4]:
# @title outputs
exp = 4581
AE = get_AE(exp)

data1 = np.array(AE['ShearStress'])
data2 = np.array([np.array(AE['TimeToStartFailure']), np.array(AE['TimeToEndFailure'])])
x = np.arange(700)

fig = make_subplots(rows=2, cols=1, row_titles=('Time To Failure','Shear Stress'))
fig.update_layout(height=800)
colors = ('red','lightblue','steelblue')
legend = ('TTsF','TTeF')
for i in np.arange(data2.shape[0]):
  fig.add_trace(go.Scatter(x=x, y=data2[i][:], mode='lines', marker=dict(color=colors[i+1]), name=legend[i]), row=1, col=1)
fig.add_trace(go.Scatter(x=x, y=data1, mode='lines', marker=dict(color=colors[0]), showlegend=False), row=2, col=1)
fig.show()

These are our outputs: our model will be inferencing the shear stress and the time to failure.
<br>We will be using as inputs the two colums `Var_Ch1` and `Var_Ch2`, that represent the acoustic emission waveform.

In [5]:
# @title inputs
plot = np.array([np.array(AE['Var_Ch1']), np.array(AE['Var_Ch2'])])

colors = ('lightpink','pink')
legend = ('Var_Ch1','Var_Ch2')

fig = make_subplots(rows=2, cols=1, row_titles=('Var_Ch1','Var_Ch2'))
fig.update_layout(height=800)
for i in np.arange(plot.shape[0]):
    fig.add_trace(go.Scatter(x=x[0:700], y=plot[i][0:700], mode='lines', marker=dict(color=colors[i]), showlegend=False), row=i+1, col=1)
fig.update_yaxes(type='log')
fig.show()

This function will prepare the dataset, given some parameters: we want to train some slightly different models, using differently preprocessed datasets.

`steps` is an hyperparameter that should represent the length of a seismic cycle (by the number of picks it covers): we assessed it empirically over the different experiments to try out different hypothesis.

We wanted to try out wether specific models performed significantly better than generic ones, and so we tried out different lengths for the seismic cycle.

In [6]:
steps = 70 # how many steps are in a seismic cycle (in average)
fraction = 0.7 # fraction of the dataset that is for training

X_train, y_train, X_test, y_test = prepare_dataset(AE, steps=steps, fraction=fraction)

The training set is the 70% of the complete dataset (that has shape (3005, 8)).

Starting from a training dataset of shape (2103, 8) we got:
- X_train with shape (2033, 70, 2);
- y_train with shape (2033,).

Our test dataset was (972, 8) and we got:
- X_test that is (902, 70, 2);
- y_test that is (902,).


# Models
Here we will be building and training all the different models we talked about in our [paper](link).

Those models are:
- a **single channel** one, that takes in input `Var_Ch1` and `Var_Ch2` together;
- a **double channel** one which takes `Var_Ch1` and `Var_Ch2` separately (to avoid "contamination", if there is any);
- an **ensemble** one made from both single and double channel models.

## Single channel

In [7]:
inp1 = Input(shape=X_train.shape[1:])

inp1 = Lambda(lambda x: tf.math.log(x))(inp1)
mod1 = BatchNormalization(axis=1)(inp1)
mod1 = LSTM(128, return_sequences=True, name='lstm')(mod1)
mod1 = Convolution1D(128, (2),activation='relu', padding='same', name='conv1')(mod1)
mod1 = Convolution1D(84, (2),activation='relu', padding='same', name='conv2')(mod1)
mod1 = Convolution1D(64, (2),activation='relu', padding='same', name='conv3')(mod1)
mod1 = Flatten()(mod1)
mod1 = Dense(64, activation='relu', name='dense1')(mod1)
mod1 = Dense(32, activation='relu', name='dense2')(mod1)

stress1 = Dense(1, activation='relu',name='regressor')(mod1)

In [8]:
model1 = models.Model(inputs=inp1, outputs=stress1)
opt = optimizers.Nadam(learning_rate=0.008)
model1.compile(optimizer=opt, loss='mean_squared_error')

# to make the output deterministic
os.environ['PYTHONHASHSEED'] = '0'
np.random.seed(1234)
rn.seed(1234)
tf.random.set_seed(1234)
session_conf = tf.compat.v1.ConfigProto(allow_soft_placement=True)
sess = tf.compat.v1.Session(graph=tf.compat.v1.get_default_graph(), config=session_conf)
K.set_session(sess)

cb_Early_Stop=EarlyStopping(monitor='val_loss',patience=25,mode='min', verbose=1) # ferma se la loss non migliora entro patience
cb_Reduce_LR = ReduceLROnPlateau(monitor='val_loss', factor=0.5, patience=5, verbose=0, mode='auto', min_delta=0.0001, cooldown=0, min_lr=0) # diminuisce il lr se la loss non migliora entro patience
callbacks = [cb_Early_Stop,cb_Reduce_LR]

In [ ]:
# @title no need to retrain (we will load it)
history1 = model1.fit(X_train, y_train, epochs=200, callbacks=callbacks, batch_size=256, verbose=1, validation_split=0.1)
model1.save_weights('eqml24/model1.weights.h5')

In [9]:
model1 = models.Model(inputs=inp1, outputs=stress1)
model1.load_weights('eqml24/model1.weights.h5')

In [ ]:
# @title losses
x = np.arange(len(history1.history['loss']))
loss = history1.history['loss']
valLoss = history1.history['val_loss']

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=loss, mode='lines', marker=dict(color='blueviolet'), name='loss'))
fig.add_trace(go.Scatter(x=x, y=valLoss, mode='lines', marker=dict(color='mediumvioletred'), name='validation loss'))
fig.update_yaxes(type='log')
fig.show()

In [10]:
# @title predictions

y_predict = model1.predict(X_test, verbose=0).reshape(-1)
x = np.arange(X_test.shape[0])

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y_predict, mode='lines', marker=dict(color='olive'), name='predictions'))
fig.add_trace(go.Scatter(x=x, y=y_test, mode='lines', marker=dict(color='black'), name='real values'))
fig.show()

rmse = error(y_predict, y_test)
print(f'\nThe Root Mean Squared Error over the test set is {rmse:0.4f}.')


The Root Mean Squared Error over the test set is 0.1433.


## Double channel

In [11]:
inp2 = Input(shape=X_train.shape[1:], name='inp')
inp2 = BatchNormalization(axis=1, name='norm')(inp2)
split = Lambda(lambda x: tf.split(x,num_or_size_splits=2,axis=2),
               output_shape = lambda s: [(s[0], s[1], s[2] // 2)] * 2,
               name='split')(inp2)

lstm1 = LSTM(128, return_sequences=True, name='lstm1')(split[0])
lstm2 = LSTM(128, return_sequences=True, name='lstm2')(split[1])

mod2 = Concatenate()([lstm1,lstm2])
mod2 = Convolution1D(128, (2),activation='relu', padding='same', name='conv1')(mod2)
mod2 = Convolution1D(64, (2),activation='relu', padding='same', name='conv2')(mod2)
mod2 = Flatten(name='flatten')(mod2)
mod2 = Dense(64, activation='relu', name='dense1')(mod2)
mod2 = Dense(32, activation='relu', name='dense2')(mod2)

stress2 = Dense(1, activation='relu', name='regressor')(mod2)

model2 = models.Model(inputs=inp2, outputs=stress2)
opt = optimizers.Nadam(learning_rate=0.004)
model2.compile(optimizer=opt, loss='mean_squared_error')

In [ ]:
# @title no need to retrain (we will load it)
history2 = model2.fit(X_train, y_train, epochs=200, callbacks=callbacks, batch_size=256, verbose=1, validation_split=0.1)
save_weights(model2,'eqml24/model2.weights.h5')

In [12]:
model2 = models.Model(inputs=inp2, outputs=stress2)
model2.load_weights('eqml24/model2.weights.h5')

In [ ]:
# @title losses
x = np.arange(len(history2.history['loss']))
loss = history2.history['loss']
valLoss = history2.history['val_loss']

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=loss, mode='lines', marker=dict(color='blueviolet'), name='loss'))
fig.add_trace(go.Scatter(x=x, y=valLoss, mode='lines', marker=dict(color='mediumvioletred'), name='validation loss'))
fig.update_yaxes(type='log')
fig.show()

In [13]:
# @title predictions
y_predict = model2.predict(X_test, verbose=0).reshape(-1)
x = np.arange(X_test.shape[0])

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=y_predict, mode='lines', marker=dict(color='olive'), name='predictions'))
fig.add_trace(go.Scatter(x=x, y=y_test, mode='lines', marker=dict(color='black'), name='real values'))
fig.show()

rmse =  error(y_predict, y_test)
print(f'\nThe Root Mean Squared Error over the test set is {rmse:0.4f}.')


The Root Mean Squared Error over the test set is 0.0629.


The **double channel** model seems to perform sligthly better overall (especially on the uprising fraction of the seismic cycle).

We found out that in this case, the `log` layer wasn't as useful as before: it made the convergence significantly slower.

## Performances

What about new and unseen data?<br>Here we will see how both models generalize on data from the other experiments.

In [14]:
data4679 = get_AE(4679)
data5198 = get_AE(5198)
X4679,y4679,_,_ = prepare_dataset(data4679,steps,1)
X5198,y5198,_,_ = prepare_dataset(data5198,steps,1)

The training set is the 100% of the complete dataset (that has shape (3005, 8)).

Starting from a training dataset of shape (63552, 8) we got:
- X_train with shape (63482, 70, 2);
- y_train with shape (63482,).

Our test dataset was (70, 8) and we got:
- X_test that is (0, 70, 2);
- y_test that is (0,).
The training set is the 100% of the complete dataset (that has shape (3005, 8)).

Starting from a training dataset of shape (3009, 8) we got:
- X_train with shape (2939, 70, 2);
- y_train with shape (2939,).

Our test dataset was (70, 8) and we got:
- X_test that is (0, 70, 2);
- y_test that is (0,).


In [15]:
pred1_4679 = model1.predict(X4679).reshape(-1)
pred2_4679 = model2.predict(X4679).reshape(-1)
pred1_5198 = model1.predict(X5198).reshape(-1)
pred2_5198 = model2.predict(X5198).reshape(-1)

1984/1984 ━━━━━━━━━━━━━━━━━━━━ 5s 3ms/step
1984/1984 ━━━━━━━━━━━━━━━━━━━━ 7s 3ms/step
92/92 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step
92/92 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step


In [16]:
# @title predictions on unseen experiments

x4679 = np.arange(X4679.shape[0])
x5198 = np.arange(X5198.shape[0])

fig = make_subplots(rows=1, cols=2, column_titles=('p4679','p5198'))
colors = ('deepskyblue','cyan','black')
legend = ('model1','model2','real data')

fig.add_trace(go.Scatter(x=x4679, y=pred1_4679, mode='lines', marker=dict(color=colors[0]), name=legend[0]), row=1, col=1)
fig.add_trace(go.Scatter(x=x4679, y=pred2_4679, mode='lines', marker=dict(color=colors[1]), name=legend[1]), row=1, col=1)
fig.add_trace(go.Scatter(x=x4679, y=y4679, mode='lines', marker=dict(color=colors[2]), name=legend[2]), row=1, col=1)

fig.add_trace(go.Scatter(x=x5198, y=pred1_5198, mode='lines', marker=dict(color=colors[0]), name=legend[0], showlegend=False), row=1, col=2)
fig.add_trace(go.Scatter(x=x5198, y=pred2_5198, mode='lines', marker=dict(color=colors[1]), name=legend[1], showlegend=False), row=1, col=2)
fig.add_trace(go.Scatter(x=x5198, y=y5198, mode='lines', marker=dict(color=colors[2]), name=legend[2], showlegend=False), row=1, col=2)

fig.show()

In [17]:
# @title RMSE
print(f'Over p4679 experiment, we get a:\n- RMSE = {error(pred1_4679, y4679)} using the single channel model;\n- RMSE = {error(pred2_4679, y4679)} with the double channel model.')
print(f'\nOver p5198 experiment, we get a:\n- RMSE = {error(pred1_5198, y5198)} using the single channel model;\n- RMSE = {error(pred2_5198, y5198)} with the double channel model.')

Over p4679 experiment, we get a:
- RMSE = 0.8879513751776104 using the single channel model;
- RMSE = 0.8192697182112112 with the double channel model.

Over p5198 experiment, we get a:
- RMSE = 0.12925077750588906 using the single channel model;
- RMSE = 0.1365416526533756 with the double channel model.


On new and unseen data from other experiments, both models do not perform as good as before (even though the double channel model does perform slightly better).

We will now try to implement a double channel **generic** model, using data from all the experiments during the training.

## Generic model

We will be training a model with a dataset with data coming from all the experiments.

In [4]:
# preparing the dataset
steps=70

exp = 4581
AE = get_AE(exp)
test = AE[int(len(AE)*0.7):]
train = AE[:int(len(AE)*0.7)]
X_test1, y_test1, _, _ = prepare_dataset(steps=steps, fraction=1, data=test, verbose=0)
X_train, y_train, X_valid, y_valid = prepare_dataset(steps=steps, fraction=0.9, data=train, verbose=0)

exp = 4679
AE = get_AE(exp)
test = AE[int(len(AE)*0.7):]
train = AE[:int(len(AE)*0.7)]
X_test2, y_test2, _, _ = prepare_dataset(steps=steps, fraction=1, data=test, verbose=0)
X1, y1, X2, y2 = prepare_dataset(steps=steps, fraction=0.9, data=train, verbose=0)
X_train = np.concatenate((X_train, X1), axis=0)
y_train = np.concatenate((y_train, y1), axis=0)
X_valid = np.concatenate((X_valid, X2), axis=0)
y_valid = np.concatenate((y_valid, y2), axis=0)

exp = 5198
AE = get_AE(exp)
test = AE[int(len(AE)*0.7):]
train = AE[:int(len(AE)*0.7)]
X_test3, y_test3, _, _ = prepare_dataset(steps=steps, fraction=1, data=test, verbose=0)
X1, y1, X2, y2 = prepare_dataset(steps=steps, fraction=0.9, data=train, verbose=0)
X_train = np.concatenate((X_train, X1), axis=0)
y_train = np.concatenate((y_train, y1), axis=0)
X_valid = np.concatenate((X_valid, X2), axis=0)
y_valid = np.concatenate((y_valid, y2), axis=0)

print(f'{len(X_train)} elements for training.\n{len(X_valid)} elements for validation.')

43614 elements for training.
4871 elements for validation.


In [5]:
# defining the model (and training)

inp3 = Input(shape=X_train.shape[1:], name='inp')
inp3 = BatchNormalization(axis=1, name='norm')(inp3)
split = Lambda(lambda x: tf.split(x,num_or_size_splits=2,axis=2),
               output_shape = lambda s: [(s[0], s[1], s[2] // 2)] * 2,
               name='split')(inp3)

lstm1 = LSTM(128, return_sequences=True, name='lstm1')(split[0])
lstm2 = LSTM(128, return_sequences=True, name='lstm2')(split[1])

mod3 = Concatenate()([lstm1,lstm2])
mod3 = Convolution1D(128, (2),activation='relu', padding='same', name='conv1')(mod3)
mod3 = Convolution1D(64, (2),activation='relu', padding='same', name='conv2')(mod3)
mod3 = Flatten(name='flatten')(mod3)
mod3 = Dense(64, activation='relu', name='dense1')(mod3)
mod3 = Dense(32, activation='relu', name='dense2')(mod3)

stress3 = Dense(1, activation='relu', name='regressor')(mod3)

model3 = models.Model(inputs=inp3, outputs=stress3)
opt = optimizers.Nadam(learning_rate=0.004)
model3.compile(optimizer=opt, loss='mean_squared_error')

In [ ]:
# @title no need to retrain (we will load it)

history3 = model3.fit(X_train, y_train, epochs=200, callbacks=callbacks, batch_size=256, verbose=1, validation_data=(X_valid, y_valid), shuffle=True)
model3.save_weights('eqml24/model3.weights.h5')

In [6]:
model3.load_weights('eqml24/model3.weights.h5')

/usr/local/lib/python3.10/dist-packages/keras/src/saving/saving_lib.py:713: UserWarning: Skipping variable loading for optimizer 'nadam', because it has 2 variables whereas the saved optimizer has 35 variables. 
  saveable.load_own_variables(weights_store.get(inner_path))


In [ ]:
# @title losses
x = np.arange(len(history3.history['loss']))
loss = history3.history['loss']
valLoss = history3.history['val_loss']

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=loss, mode='lines', marker=dict(color='blueviolet'), name='loss'))
fig.add_trace(go.Scatter(x=x, y=valLoss, mode='lines', marker=dict(color='mediumvioletred'), name='validation loss'))
fig.update_yaxes(type='log')
fig.show()

In [7]:
y1_predict = model3.predict(X_test1).reshape(-1)
y2_predict = model3.predict(X_test2).reshape(-1)
y3_predict = model3.predict(X_test3).reshape(-1)

26/26 ━━━━━━━━━━━━━━━━━━━━ 2s 5ms/step
594/594 ━━━━━━━━━━━━━━━━━━━━ 3s 5ms/step
27/27 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step


In [8]:
# @title predictions

fig = make_subplots(rows=3, cols=1, row_titles=('p4581','p4679','p5198'))
# fig.update_layout(title=dict(text=f'Inputs'))
colors = ('olive','black')
legend = ('predictions','real data')

x = [np.arange(X_test1.shape[0]), np.arange(X_test2.shape[0]), np.arange(X_test3.shape[0])]
predicts = [y1_predict, y2_predict, y3_predict]
real_data = [y_test1, y_test2, y_test3]

for i in range(len(x)):
  check = True if i == 0 else False
  fig.add_trace(go.Scatter(x=x[i], y=predicts[i], mode='lines', marker=dict(color=colors[0]), name=legend[0], showlegend=check), row=i+1, col=1)
  fig.add_trace(go.Scatter(x=x[i], y=real_data[i], mode='lines', marker=dict(color=colors[1]), name=legend[1], showlegend=check), row=i+1, col=1)

fig.update_layout(height=1500)

fig.show()

print(f'\nThe Root Mean Squared Error:\n- over p4581 is {error(y1_predict, y_test1):0.4f};\n- over p4679 is {error(y2_predict, y_test2):0.4f};\n- over p5198 is {error(y3_predict, y_test3):0.4f}.')


The Root Mean Squared Error:
- over p4581 is 0.0659;
- over p4679 is 0.0248;
- over p5198 is 0.0241.


The experiment p4581 seems to be worst performing one (the acoustic emissions were the most noisy ones).

The model seems able to generalize to different experiment conditions without great difficulty (as the **RMSE** remain on the same magnitude order of `model2`): so, the greatest and more varied the dataset, the better are the predictions.